# Processing the Data for d3 JSON files

This notebook was used to take our data and make it into the specific JSON format that we needed for the dragit.js package we were using for our d3 visualizations

In [2]:
import numpy as np
import pandas as pd

import seaborn as sns
%matplotlib inline
sns.set(style="ticks")

pp = pd.read_csv('data/party-partisanship.csv')
part = pd.read_csv('data/partisans.csv')
pmembership = pd.read_csv('data/party_membership.csv')

import matplotlib.pyplot as plt

In [3]:
# the number of parties in each session
numparties = {}

for index,row in pp.iterrows():
    num = 0
    for col in row.keys():
        if row[col] > 0:
            num+=1
    numparties[index+1] = num


In [4]:
# create the timecube json for the partisanship visual
timecube = {}

for i in range(0,113):
    sesslist = []
    row = pmembership.iloc[i]
    row2 = pp.iloc[i]
    top2 = []
    rowcopy = row.copy()
    top2.append(row.argmax())
    top2.append(rowcopy.argmax(rowcopy.pop(row.argmax())))
    
    # keep Dems on the left and Repubs on the right
    if 'Democrat' in top2 and 'Republican' in top2:
        sesslist.append({'party':'Democrat', 'vals':{}})
        sesslist.append({'party':'Republican', 'vals':{}})
    elif 'Democrat' in top2:
        other = top2[0] if top2[1]=='Democrat' else top2[1]
        sesslist.append({'party':'Democrat', 'vals':{}})
        sesslist.append({'party':other, 'vals':{}})
    elif 'Republican' in top2:
        other = top2[0] if top2[1]=='Republican' else top2[1]
        sesslist.append({'party':other, 'vals':{}})
        sesslist.append({'party':'Republican', 'vals':{}})
    else:
        sesslist.append({'party':top2[0], 'vals':{}})
        sesslist.append({'party':top2[1], 'vals':{}})
        
    for party in row2.keys():
        if party not in top2:
            if row2[party] > 0:
                sesslist.append({'party':party, 'vals':{}})
    
    for partydata in sesslist:
        party = partydata['party']
        partydata['vals']['t'] = i
        partydata['vals']['num'] = pmembership.iloc[i].loc[party]
        partydata['vals']['unification'] = pp.iloc[i].loc[party]
        partydata['vals']['majority'] = part.iloc[i].loc['majority']
        
    print sesslist
    
    timecube[str(i+1)] = sesslist


[{'vals': {'majority': 0.13, 'num': 23, 'unification': 0.059999999999999998, 't': 0}, 'party': 'Federalist'}, {'vals': {'majority': 0.13, 'num': 18, 'unification': 0.27000000000000002, 't': 0}, 'party': 'Republican'}, {'vals': {'majority': 0.13, 'num': 5, 'unification': 0.17000000000000001, 't': 0}, 'party': 'Anti-Administration'}, {'vals': {'majority': 0.13, 'num': 10, 'unification': 0.54000000000000004, 't': 0}, 'party': 'Pro-Administration'}]
[{'vals': {'majority': 0.070000000000000007, 'num': 30, 'unification': 0.10000000000000001, 't': 1}, 'party': 'Federalist'}, {'vals': {'majority': 0.070000000000000007, 'num': 25, 'unification': 0.14000000000000001, 't': 1}, 'party': 'Republican'}, {'vals': {'majority': 0.070000000000000007, 'num': 6, 'unification': 0.029999999999999999, 't': 1}, 'party': 'Anti-Administration'}, {'vals': {'majority': 0.070000000000000007, 'num': 6, 'unification': 0.070000000000000007, 't': 1}, 'party': 'Pro-Administration'}]
[{'vals': {'majority': 0.14000000000

In [16]:
# dump json
with open('timecubedata.json','w') as f:
    json.dump(timecube, f)

In [16]:
# make the timecube for the party membership visual
leg = pd.read_csv('data/legislators.csv')

for i,v in leg['c1'].iteritems():
    if v == 1:
        print leg.last_name.iloc[i]

Bassett
Bland
Burke
Carroll
Clymer
Contee
Dalton
Elmer
Few
Floyd
Gale
Grayson
Grout
Hawkins
Huntington
Izard
Johnson
Johnston
Lee
Maclay
Mathews
Morris
Partridge
Paterson
Smith
Stone
Van Rensselaer
Wynkoop
Dickinson
Walker
Ashe
Carroll
Ellsworth
Gerry
Huger
Read
Seney
Sherman
Silvester
Steele
Sturges
Tucker
White
Williamson
Boudinot
Cadwalader
Fitzsimons
Griffin
Lee
Scott
Strong
Vining
Wadsworth
Wingate
Ames
Bloodworth
Bourne
Coles
Gunn
Hathorn
Henry
Langdon
Leonard
Muhlenberg
Page
Trumbull
Goodhue
Laurance
Foster
Schuyler
Sinnickson
Smith
Brown
Hartley
Livermore
Parker
Sedgwick
Thatcher
Foster
Jackson
Muhlenberg
Butler
Hiester
Moore
Baldwin
Stanton
Sumter
Madison
Giles
Gilman
Benson
Schureman
Sevier
Monroe
King


In [5]:
mtc = {} # membership timecube
leg = pd.read_csv('data/legislators.csv', encoding='iso-8859-1')

for j in range(0,113):
    sesslist = []
    
    for i,v in leg['c'+str(j+1)].iteritems():
        if v == 1:
#             print i
            sesslist.append({
                "party":leg.party.iloc[i],
                "lastname":leg.last_name.iloc[i].encode('utf-8'),
                "firstname":leg.first_name.iloc[i].encode('utf-8'),
                "state":leg.state.iloc[i],
                "type":leg.type.iloc[i],
            })
                
    mtc[str(j+1)] = sesslist
print mtc

{'24': [{'party': u'Adams', 'state': u'IN', 'type': u'sen', 'firstname': 'William', 'lastname': 'Hendricks'}, {'party': u'Jackson', 'state': u'NH', 'type': u'sen', 'firstname': 'Isaac', 'lastname': 'Hill'}, {'party': u'Jackson', 'state': u'AL', 'type': u'sen', 'firstname': 'Gabriel', 'lastname': 'Moore'}, {'party': u'Anti-Jacksonian', 'state': u'CT', 'type': u'sen', 'firstname': 'Gideon', 'lastname': 'Tomlinson'}, {'party': u'Democrat', 'state': u'IN', 'type': u'sen', 'firstname': 'John', 'lastname': 'Tipton'}, {'party': u'Whig', 'state': u'MS', 'type': u'sen', 'firstname': 'John', 'lastname': 'Black'}, {'party': u'Whig', 'state': u'MD', 'type': u'sen', 'firstname': 'Joseph', 'lastname': 'Kent'}, {'party': u'Democrat', 'state': u'PA', 'type': u'sen', 'firstname': 'Samuel', 'lastname': 'McKean'}, {'party': u'Democrat', 'state': u'OH', 'type': u'sen', 'firstname': 'Thomas', 'lastname': 'Morris'}, {'party': nan, 'state': u'DE', 'type': u'sen', 'firstname': 'Arnold', 'lastname': 'Naudain'}

In [6]:
import json
with open('membershiptimecube2.json','w') as f:
    json.dump(mtc, f)